In [1]:
import warnings
warnings.filterwarnings('ignore')

from IPython.display import display, HTML
display(HTML("<style>.container { width:80% !important; }</style>"))

## Text Mining with Classification 
Demo Notebook for Text Mining and using with Classification (RandomForest)

See blog post https://oralytics.com/2021/11/01/combining-nlp-and-machine-learning-for-document-classification/

In [2]:
import numpy as np
import re
import nltk
from sklearn.datasets import load_files
import pickle
from nltk.corpus import stopwords

#Run the following the first time you run the notebook. After that just comment them out
#nltk.download('wordnet')
#nltk.download('omw-1.4')
#nltk.download('stopwords')


In [3]:
#The dataset used for this demo can be downloaded from the Cornell Natural Language Processing Group. 
#The dataset consists of a total of 2000 documents. 
#Half of the documents contain positive reviews regarding a movie 
# while the remaining half contains negative reviews. 
#Further details regarding the dataset can be found at 
#       http://www.cs.cornell.edu/people/pabo/movie-review-data/poldata.README.2.0.txt 

#Donwload & extract the dataset. 
#Open the folder "txt_sentoken". Take a note of this directory as it will be used later
#The folder contains two subfolders: "neg" and "pos". 
#If you open these folders, you can see the text documents containing movie reviews.

#This dataset will allow use to perform a type of Sentiment Analysis
source_file_dir = r"/Users/brendan.tierney/Dropbox/4-Datasets/review_polarity/txt_sentoken"

In [4]:
#The load_files function automatically divides the dataset into data and target sets.
#load_files  will treat each folder inside the "txt_sentoken" folder as one category 
#  and all the documents inside that folder will be assigned its corresponding category.
movie_data = load_files(source_file_dir)
X, y = movie_data.data, movie_data.target

#load_files  function loads the data from both "neg" and "pos" folders into the X variable, 
#  while the target categories are stored in y

In [5]:
movie_data

{'data': [b"arnold schwarzenegger has been an icon for action enthusiasts , since the late 80's , but lately his films have been very sloppy and the one-liners are getting worse . \nit's hard seeing arnold as mr . freeze in batman and robin , especially when he says tons of ice jokes , but hey he got 15 million , what's it matter to him ? \nonce again arnold has signed to do another expensive blockbuster , that can't compare with the likes of the terminator series , true lies and even eraser . \nin this so called dark thriller , the devil ( gabriel byrne ) has come upon earth , to impregnate a woman ( robin tunney ) which happens every 1000 years , and basically destroy the world , but apparently god has chosen one man , and that one man is jericho cane ( arnold himself ) . \nwith the help of a trusty sidekick ( kevin pollack ) , they will stop at nothing to let the devil take over the world ! \nparts of this are actually so absurd , that they would fit right in with dogma . \nyes , th

In [6]:
X

[b"arnold schwarzenegger has been an icon for action enthusiasts , since the late 80's , but lately his films have been very sloppy and the one-liners are getting worse . \nit's hard seeing arnold as mr . freeze in batman and robin , especially when he says tons of ice jokes , but hey he got 15 million , what's it matter to him ? \nonce again arnold has signed to do another expensive blockbuster , that can't compare with the likes of the terminator series , true lies and even eraser . \nin this so called dark thriller , the devil ( gabriel byrne ) has come upon earth , to impregnate a woman ( robin tunney ) which happens every 1000 years , and basically destroy the world , but apparently god has chosen one man , and that one man is jericho cane ( arnold himself ) . \nwith the help of a trusty sidekick ( kevin pollack ) , they will stop at nothing to let the devil take over the world ! \nparts of this are actually so absurd , that they would fit right in with dogma . \nyes , the film is

In [7]:
y

array([0, 1, 1, ..., 1, 0, 0])

In [8]:
documents = []

from nltk.stem import WordNetLemmatizer

stemmer = WordNetLemmatizer()

for sen in range(0, len(X)):
    # Remove all the special characters, numbers, punctuation 
    document = re.sub(r'\W', ' ', str(X[sen]))
    
    # remove all single characters
    document = re.sub(r'\s+[a-zA-Z]\s+', ' ', document)
    
    # Remove single characters from the start of document with a space
    document = re.sub(r'\^[a-zA-Z]\s+', ' ', document) 
    
    # Substituting multiple spaces with single space
    document = re.sub(r'\s+', ' ', document, flags=re.I)
    
    # Removing prefixed 'b'
    document = re.sub(r'^b\s+', '', document)
    
    # Converting to Lowercase
    document = document.lower()
    
    # Lemmatization
    document = document.split()

    document = [stemmer.lemmatize(word) for word in document]
    document = ' '.join(document)
    
    documents.append(document)

In [9]:
#Create bag of words

In [10]:
#max_features = maximum number of words to use across all documents.
#min_df = the minimum number of documents that should contain this feature. 
#   Only include words that occur in at least, for example, 5 documents. 
#max_df = the fraction/percentage of documents where the word is contained. 
#   Here 0.7 means that we should include only those words that occur in a maximum of 70% of all the documents. 
#   Words that occur in almost every document are usually not suitable for classification because 
#      they do not provide any unique information about the document.
#
#stop_words = words to remove from the curpos, stop words may not contain any useful information.

from sklearn.feature_extraction.text import CountVectorizer

vectorizer = CountVectorizer(max_features=1500, min_df=5, max_df=0.7, stop_words=stopwords.words('english'))
X = vectorizer.fit_transform(documents).toarray()

In [11]:
X

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 1, 0],
       ...,
       [0, 0, 0, ..., 1, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [2, 0, 0, ..., 1, 0, 0]])

In [12]:
#The bag of words approach works fine for converting text to numbers. However, it has one drawback. 
#It assigns a score to a word based on its occurrence in a particular document. It doesn't take into 
#account the fact that the word might also be having a high frequency of occurrence in other documents 
#as well. TFIDF resolves this issue by multiplying the term frequency of a word by the inverse document 
#frequency. The TF stands for "Term Frequency" while IDF stands for "Inverse Document Frequency".
#
#The term frequency is calculated as:
# Term frequency = (Number of Occurrences of a word)/(Total words in the document)

#And the Inverse Document Frequency is calculated as:
# IDF(word) = Log((Total number of documents)/(Number of documents containing the word))


In [13]:
#The TFIDF value for a word in a particular document is higher if the frequency of occurrence of that 
#word is higher in that specific document but lower in all the other documents.

#To convert values obtained using the bag of words model into TFIDF values, execute the following script:

from sklearn.feature_extraction.text import TfidfTransformer
tfidfconverter = TfidfTransformer()
X = tfidfconverter.fit_transform(X).toarray()

#Alteratively, could have run the following, to replace above code and previous Vectorization code
# from sklearn.feature_extraction.text import TfidfVectorizer
# tfidfconverter = TfidfVectorizer(max_features=1500, min_df=5, max_df=0.7, stop_words=stopwords.words('english'))
# X = tfidfconverter.fit_transform(documents).toarray()

In [14]:
X

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.07349223,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.05424743, 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.1232798 , 0.        , 0.        , ..., 0.05277153, 0.        ,
        0.        ]])

In [15]:
#Divide the data into training and test datasets

In [16]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)
#Train DS = 70%
#Test DS = 30%


In [17]:
##### Import Random Forest Model
#Use RandomForest algorithm to create a model
# n_estimators = number of trees in the Forest

from sklearn.ensemble import RandomForestClassifier
classifier = RandomForestClassifier(n_estimators=1000, random_state=0)
classifier.fit(X_train, y_train) 

RandomForestClassifier(n_estimators=1000, random_state=0)

In [18]:
#Now label/classify the Test DS
y_pred = classifier.predict(X_test)

In [19]:
#Evaluate the model
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

print("Accuracy:", accuracy_score(y_test, y_pred))
print(confusion_matrix(y_test,y_pred))
print(classification_report(y_test,y_pred))

Accuracy: 0.855
[[180  28]
 [ 30 162]]
              precision    recall  f1-score   support

           0       0.86      0.87      0.86       208
           1       0.85      0.84      0.85       192

    accuracy                           0.85       400
   macro avg       0.85      0.85      0.85       400
weighted avg       0.85      0.85      0.85       400



In [20]:
#Save the model to use another time (without retraining) or to use in another environment
rf_model_file_name = "/Users/brendan.tierney/Dropbox/4-Datasets/review_polarity/rf_model_file"
with open(rf_model_file_name, 'wb') as picklefile:
    pickle.dump(classifier,picklefile)
    

In [21]:
#To load the model from the file and use it on a dataset
with open(rf_model_file_name, 'rb') as training_model:
    rf_model = pickle.load(training_model)

In [22]:
#now use the model to make predictions
y_pred2 = rf_model.predict(X_test)

print(confusion_matrix(y_test, y_pred2))
print(classification_report(y_test, y_pred2))
print(accuracy_score(y_test, y_pred2)) 

[[180  28]
 [ 30 162]]
              precision    recall  f1-score   support

           0       0.86      0.87      0.86       208
           1       0.85      0.84      0.85       192

    accuracy                           0.85       400
   macro avg       0.85      0.85      0.85       400
weighted avg       0.85      0.85      0.85       400

0.855
